# Astroplan in CoCalc

Installed in Jupyter's "Python 3 (Ubuntu Linux)" kernel.

https://astroplan.readthedocs.io/

In [1]:
import astroplan
astroplan.__version__

'0.4'

In [2]:
from astropy.coordinates import SkyCoord
from astroplan import FixedTarget

In [3]:
altair = FixedTarget.from_name('Altair')
from astroplan import Observer
observer = Observer.at_site('subaru')

 [Done]


In [6]:
from astroplan import Observer, FixedTarget
from astropy.time import Time
time_range = Time(["2015-08-01 06:00", "2015-08-01 12:00"])

In [8]:
%%writefile targets.txt
# name ra_degrees dec_degrees
Polaris 37.95456067 89.26410897
Vega 279.234734787 38.783688956
Albireo 292.68033548 27.959680072
Algol 47.042218553 40.955646675
Rigel 78.634467067 -8.201638365
Regulus 152.092962438 11.967208776

Writing targets.txt


In [9]:
# Read in the table of targets
from astropy.table import Table
target_table = Table.read('targets.txt', format='ascii')

# Create astroplan.FixedTarget objects for each one in the table
from astropy.coordinates import SkyCoord
import astropy.units as u
targets = [FixedTarget(coord=SkyCoord(ra=ra*u.deg, dec=dec*u.deg), name=name)
           for name, ra, dec in target_table]
targets

[<FixedTarget "Polaris" at SkyCoord (ICRS): (ra, dec) in deg (37.95456067, 89.26410897)>,
 <FixedTarget "Vega" at SkyCoord (ICRS): (ra, dec) in deg (279.23473479, 38.78368896)>,
 <FixedTarget "Albireo" at SkyCoord (ICRS): (ra, dec) in deg (292.68033548, 27.95968007)>,
 <FixedTarget "Algol" at SkyCoord (ICRS): (ra, dec) in deg (47.04221855, 40.95564667)>,
 <FixedTarget "Rigel" at SkyCoord (ICRS): (ra, dec) in deg (78.63446707, -8.20163837)>,
 <FixedTarget "Regulus" at SkyCoord (ICRS): (ra, dec) in deg (152.09296244, 11.96720878)>]

In [10]:
from astroplan import (AltitudeConstraint, AirmassConstraint,
                       AtNightConstraint)
constraints = [AltitudeConstraint(10*u.deg, 80*u.deg),
               AirmassConstraint(5), AtNightConstraint.twilight_civil()]


In [13]:
from astroplan import is_observable, is_always_observable, months_observable
# Are targets *ever* observable in the time range?
ever_observable = is_observable(constraints, subaru, targets, time_range=time_range)

# Are targets *always* observable in the time range?
always_observable = is_always_observable(constraints, subaru, targets, time_range=time_range)

# During what months are the targets ever observable?
best_months = months_observable(constraints, subaru, targets)

In [14]:
from astroplan import download_IERS_A
download_IERS_A()

 [Done]


In [15]:
from astropy.table import Table
import numpy as np
observability_table = Table()
observability_table['targets'] = [target.name for target in targets]
observability_table['ever_observable'] = ever_observable
observability_table['always_observable'] = always_observable
print(observability_table)

targets ever_observable always_observable
------- --------------- -----------------
Polaris            True              True
   Vega            True              True
Albireo            True             False
  Algol            True             False
  Rigel           False             False
Regulus           False             False


In [16]:
from astroplan import observability_table
table = observability_table(constraints, subaru, targets, time_range=time_range)
print(table)

target name ever observable always observable fraction of time observable
----------- --------------- ----------------- ---------------------------
    Polaris            True              True                         1.0
       Vega            True              True                         1.0
    Albireo            True             False          0.8333333333333334
      Algol            True             False         0.16666666666666666
      Rigel           False             False                         0.0
    Regulus           False             False                         0.0


In [22]:
import matplotlib.pyplot as plt
from matplotlib import cm
from astroplan.plots import plot_sky

from astroplan import time_grid_from_range
time_range = Time(["2015-08-01 06:00", "2015-08-01 12:00"])
time_grid = time_grid_from_range(time_range)

plt.figure(figsize=(10,10))
cmap = cm.Set1             # Cycle through this colormap

for i, target in enumerate(targets):
    ax = plot_sky(target, subaru, time_grid,
                  style_kwargs=dict(color=cmap(float(i)/len(targets)),
                                    label=target.name))

legend = ax.legend(loc='lower center')
legend.get_frame().set_facecolor('w')
plt.show()

/usr/local/lib/python3.5/dist-packages/matplotlib/cbook/deprecation.py:106: MatplotlibDeprecationWarning: The frac parameter was deprecated in version 2.1. Use tick padding via Axes.tick_params instead.
  warnings.warn(message, mplDeprecation, stacklevel=1)
